In [1]:
import pandas as pd
import numpy as np
import geopandas as gpd
import matplotlib.pyplot as plt
from pathlib import Path
from shapely.geometry import box, Point, Polygon
import xarray as xr
import rioxarray
from rasterio.features import shapes
import os
import folium
from geocube.api.core import make_geocube
from src.utils import read_neon_trees

root = Path.cwd()

In [3]:
trees = read_neon_trees(root, 'BART', 26919) 
trees['dbh_inches'] = trees['stemDiameter']/2.54

In [59]:
trees.to_file(root / 'output' /'BART'/'all_trees_BART.gpkg')

In [3]:
dbh_column = 'dbh_inches'
epsg = 26919
sentinel_filename = '2019_bart'
species_colname = 'taxonID'
beech_code = 'FAGR'

# read in sentinel
r = xr.open_dataarray(root /'sentinel_data' /f'{sentinel_filename}.nc')
r = r.rio.write_crs(epsg).rio.set_spatial_dims(x_dim="x",y_dim="y",).rio.write_coordinate_system()
r1 = r.isel(band=1,time=1)
# read in tree points
# trees = gpd.read_file(root / 'suny' / 'tree_points_2016_2013.gpkg')
# trees = trees.to_crs(epsg)

# vectorize raster
polygons = shapes(r1.values, transform=r1.rio.transform())
# Create a list of dictionaries for each polygon
geometry = []
ids = []
i = 1
for polygon, value in polygons:
        geometry.append(polygon)
        ids.append(i)
        i += 1   

# Create a GeoDataFrame from the features
gdf_dict = {'geometry':[Polygon(x['coordinates'][0]) for x in geometry],'cell_id':list(range(1,len(geometry)+1))}

gdf = gpd.GeoDataFrame(gdf_dict, crs=r1.rio.crs)
gdf = gdf.loc[gdf.area <=100]

# join tree points to polygons
j = gpd.sjoin(gdf, trees, predicate='contains')



In [21]:
# dbh in inches gives basal area in sqare feet
j['basal_area'] = .005454 * j[dbh_column]**2

# make beech basal area column
j['beech_basal_area'] = j.apply(lambda row: row['basal_area'] if row[species_colname] == beech_code else 0, axis=1)

# get total basal area per per pixel
total_beech_basal_area = j.groupby(['cell_id'])['beech_basal_area'].sum().reset_index()
total_basal_area = j.groupby(['cell_id'])['basal_area'].sum().reset_index()

# join result back to spatial data
beech_merged1 = gdf.merge(total_basal_area,on='cell_id',how='inner')
beech_merged = beech_merged1.merge(total_beech_basal_area,on='cell_id',how='inner')
# convert basal area sq.ft to sq. meters
beech_merged['beech_basal_area'] = beech_merged['beech_basal_area']/10.764
beech_merged['basal_area'] = beech_merged['basal_area']/10.764

# # get percent basal area per 100 sq. meter pixel
beech_merged['percent_beech_basal_area'] = (beech_merged['beech_basal_area']/beech_merged['basal_area'])*100

g = make_geocube(
vector_data=beech_merged,
measurements=["percent_beech_basal_area"],
like=r1, # ensure the data are on the same grid
)

In [23]:
print(f"total number of raster cells: {gdf.shape[0]} \n number of trees: {j.shape[0]} \n number of unique cells: {beech_merged.shape[0]}")

total number of raster cells: 126571 
 number of trees: 1622 
 number of unique cells: 411


In [24]:
g.to_netcdf(root / 'output' / 'BART' / 'percent_basal_area_BART.nc')

In [ ]:
t = xr.open_dataset(root / 'output' / 'BART' / f'percent_basal_area_BART.nc')

t['percent_beech_basal_area'].plot()

In [ ]:
filt = gpd.read_file(root / 'output' / 'BART' / 'filtered_trees_BART.gpkg')

filt.head()

In [8]:
sun_beech = filt.loc[(filt['taxonID']=='FAGR') & (filt['canopyPosition'] == 'Full sun')]

sun_beech.shape

(15, 17)

In [45]:
cc = tuple(trees.to_crs(4326).geometry.get_coordinates().iloc[0,:])[::-1]
m = folium.Map(location= cc, zoom_start=11)



folium.GeoJson(
    j.to_crs(4326)
).add_to(m)

folium.GeoJson(
    trees.to_crs(4326),
    marker=folium.Circle(radius=2, fill_color="orange", fill_opacity=0.4, color="red", weight=1)
).add_to(m)

m
